# Pulling Data

Let's use Google Cloud and BigQuery to pull this data from GDETL. Specifically, let's pull data from `GDELT Global Event Database (GDELT 1.0)`

I created this notebook so that I can isloate my SQL queuries from the rest of my code. This notebook will focus on querying a larger feature data set that we can use to pull for our model to help with predictions.

In [1]:
# Set up the env.
#%conda init
#%conda env list ## to see the availble options
#%conda activate civil_unrest ## to activate the targeted env

In [2]:
# Import the necessary module
from google.cloud import bigquery
from matplotlib import pyplot as plt
import folium
from matplotlib import colors
from geopy.distance import geodesic


---
## Pulling Data
Let's use Google Cloud and BigQuery to pull this data from GDETL. Specifically, let's pull data from `GDELT Global Event Database (GDELT 1.0)`

---

---

Later I'll realize that I'd like to know exactly what time of day the events occur at. This would require upgrading to `GDELT 2.0`. This is something I'll leave to further improvements to my model. I may conduct this in the future.

---

In [3]:
# Log in to Google Cloud
#!gcloud auth application-default login

In [4]:
# Initialize BigQuery client with the project ID
client = bigquery.Client(project="civil-unrest-predictor")

query = """
SELECT
    SQLDATE,
    EventCode,
    ActionGeo_FullName,
    ActionGeo_Lat,
    ActionGeo_Long,
    AvgTone
FROM
    `gdelt-bq.full.events`
WHERE
    EventCode IN ('145', '1451', '1452', '1453', '1454')
    AND ActionGeo_FullName LIKE '%Chicago%'
    AND CAST(SQLDATE AS STRING) >= '20150101'
ORDER BY
    SQLDATE DESC
LIMIT 10000;
"""

# Execute the updated query
query_job = client.query(query)

# Convert results to a DataFrame
data = query_job.result().to_dataframe()


---

Later I'll realize that I'd like to know exactly what time of day the events occur at. This would require upgrading to `GDELT 2.0`. This is something I'll leave to further improvements to my model. I may conduct this in the future.

---

In [5]:
data

SQLDATE EventCode                              ActionGeo_FullName  \
0     20241211       145                Chicago, Illinois, United States   
1     20241211       145                Chicago, Illinois, United States   
2     20241206       145                Chicago, Illinois, United States   
3     20241202       145  University Of Chicago, Illinois, United States   
4     20241202       145                Chicago, Illinois, United States   
...        ...       ...                                             ...   
3344  20150119       145                Chicago, Illinois, United States   
3345  20150119       145                Chicago, Illinois, United States   
3346  20150119       145                Chicago, Illinois, United States   
3347  20150119       145                Chicago, Illinois, United States   
3348  20150108       145                Chicago, Illinois, United States   

      ActionGeo_Lat  ActionGeo_Long   AvgTone  
0           41.8500        -87.6501 -4.147465  
1           41.8500        -87.6501 -4.147465  
2           41.8500        -87.6501  1.066667  
3           41.7898        -87.5998 -0.843289  
4           41.8500        -87.6501 -7.840083  
...             ...             ...       ...  
3344        41.8500        -87.6501  2.494577  
3345        41.8500        -87.6501  2.857143  
3346        41.8500        -87.6501  2.494577  
3347        41.8500        -87.6501  2.494577  
3348        41.8500        -87.6501  2.007772  

[3349 rows x 6 columns]

---

For some reason, the following is not included in the initial set, so we'll ensure we have the correct regions for our data. I might change this later.

Let's make sure we have the right location for the data. Let's pull in the target location information.

---

In [6]:
import pandas as pd
target_location = pd.read_csv('csv/target_location.csv')
target_location

start_lat  start_lon    end_lat    end_lon
0  41.865756 -87.684843  41.918433 -87.617952

In [7]:
start_lat = target_location['start_lat'].values[0]
end_lat = target_location['end_lat'].values[0]
start_lon = target_location['start_lon'].values[0]
end_lon = target_location['end_lon'].values[0]

query = f"""
SELECT
    SQLDATE,
    EventCode,
    ActionGeo_FullName,
    ActionGeo_Lat,
    ActionGeo_Long,
    AvgTone
FROM
    `gdelt-bq.full.events`
WHERE
    EventCode IN ('145', '1451', '1452', '1453', '1454')
    AND ActionGeo_Lat BETWEEN {start_lat} AND {end_lat}
    AND ActionGeo_Long BETWEEN {start_lon} AND {end_lon}
    AND CAST(SQLDATE AS STRING) >= '20150101'
ORDER BY
    SQLDATE DESC
LIMIT 10000;
"""

# Execute the updated query
query_job = client.query(query)

# Convert results to a DataFrame
label_data = query_job.result().to_dataframe()

In [8]:
label_data

SQLDATE EventCode                                 ActionGeo_FullName  \
0    20240823       145                Union Park, Illinois, United States   
1    20240822       145                Union Park, Illinois, United States   
2    20240820       145                Union Park, Illinois, United States   
3    20240820       145                Union Park, Illinois, United States   
4    20240627       145       Buckingham Fountain, Illinois, United States   
..        ...       ...                                                ...   
142  20160320       145  University Of Illinois At Chicago, Illinois, U...   
143  20160313       145  University Of Illinois At Chicago, Illinois, U...   
144  20160313       145  University Of Illinois At Chicago, Illinois, U...   
145  20160312       145              Chicago Loop, Illinois, United States   
146  20151225       145         Water Tower Place, Illinois, United States   

     ActionGeo_Lat  ActionGeo_Long    AvgTone  
0          41.8839        -87.6648  -3.046968  
1          41.8839        -87.6648   0.000000  
2          41.8839        -87.6648  -4.319654  
3          41.8839        -87.6648  -4.319654  
4          41.8756        -87.6189  -7.052186  
..             ...             ...        ...  
142        41.8720        -87.6492  -7.417219  
143        41.8720        -87.6492  -8.571429  
144        41.8720        -87.6492  -8.571429  
145        41.8811        -87.6298  -2.366864  
146        41.8978        -87.6237 -12.850954  

[147 rows x 6 columns]

---

It'll be easier to have everything in datetime, not SQLDATE. Rename the df column and change all the data.

---

In [9]:
combined_data = pd.concat([label_data, data], ignore_index=True)
combined_data

SQLDATE EventCode                            ActionGeo_FullName  \
0     20240823       145           Union Park, Illinois, United States   
1     20240822       145           Union Park, Illinois, United States   
2     20240820       145           Union Park, Illinois, United States   
3     20240820       145           Union Park, Illinois, United States   
4     20240627       145  Buckingham Fountain, Illinois, United States   
...        ...       ...                                           ...   
3491  20150119       145              Chicago, Illinois, United States   
3492  20150119       145              Chicago, Illinois, United States   
3493  20150119       145              Chicago, Illinois, United States   
3494  20150119       145              Chicago, Illinois, United States   
3495  20150108       145              Chicago, Illinois, United States   

      ActionGeo_Lat  ActionGeo_Long   AvgTone  
0           41.8839        -87.6648 -3.046968  
1           41.8839        -87.6648  0.000000  
2           41.8839        -87.6648 -4.319654  
3           41.8839        -87.6648 -4.319654  
4           41.8756        -87.6189 -7.052186  
...             ...             ...       ...  
3491        41.8500        -87.6501  2.494577  
3492        41.8500        -87.6501  2.857143  
3493        41.8500        -87.6501  2.494577  
3494        41.8500        -87.6501  2.494577  
3495        41.8500        -87.6501  2.007772  

[3496 rows x 6 columns]

In [10]:
# Convert SQLDATE to datetime
combined_data['Date'] = pd.to_datetime(combined_data['SQLDATE'], format='%Y%m%d')

# Drop the old SQLDATE column
combined_data.drop(columns=['SQLDATE'], inplace=True)

# Reorder the columns to make 'Date' the first column
combined_data = combined_data[['Date', 'EventCode', 'ActionGeo_FullName', 'ActionGeo_Lat', 'ActionGeo_Long', 'AvgTone']]

# Display the updated DataFrame
combined_data

Date EventCode                            ActionGeo_FullName  \
0    2024-08-23       145           Union Park, Illinois, United States   
1    2024-08-22       145           Union Park, Illinois, United States   
2    2024-08-20       145           Union Park, Illinois, United States   
3    2024-08-20       145           Union Park, Illinois, United States   
4    2024-06-27       145  Buckingham Fountain, Illinois, United States   
...         ...       ...                                           ...   
3491 2015-01-19       145              Chicago, Illinois, United States   
3492 2015-01-19       145              Chicago, Illinois, United States   
3493 2015-01-19       145              Chicago, Illinois, United States   
3494 2015-01-19       145              Chicago, Illinois, United States   
3495 2015-01-08       145              Chicago, Illinois, United States   

      ActionGeo_Lat  ActionGeo_Long   AvgTone  
0           41.8839        -87.6648 -3.046968  
1           41.8839        -87.6648  0.000000  
2           41.8839        -87.6648 -4.319654  
3           41.8839        -87.6648 -4.319654  
4           41.8756        -87.6189 -7.052186  
...             ...             ...       ...  
3491        41.8500        -87.6501  2.494577  
3492        41.8500        -87.6501  2.857143  
3493        41.8500        -87.6501  2.494577  
3494        41.8500        -87.6501  2.494577  
3495        41.8500        -87.6501  2.007772  

[3496 rows x 6 columns]

---

Ok now let's plot it in the region we pulled the data from to ensure it's the correct data.

---

In [11]:
# Define a colormap
colormap = plt.colormaps.get_cmap('Reds')

# Normalize the AvgTone values to the range [0, 1] and invert the colormap
norm = colors.Normalize(vmin=-combined_data['AvgTone'].max(), vmax=-combined_data['AvgTone'].min())

# Create a map centered around the average latitude and longitude
m = folium.Map(location=[combined_data['ActionGeo_Lat'].mean(), combined_data['ActionGeo_Long'].mean()], zoom_start=4)

# Add markers for each event in the combined_data DataFrame
for index, row in combined_data.iterrows():
    # Get the color based on the normalized AvgTone value
    color = colors.rgb2hex(colormap(norm(-row['AvgTone'])))
    folium.Circle(
        location=[row['ActionGeo_Lat'], row['ActionGeo_Long']],
        radius=100,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        popup=f"Date: {row['Date']}, EventCode: {row['EventCode']}, AvgTone: {row['AvgTone']}"
    ).add_to(m)

# Get the minimum and maximum latitude and longitude
min_lat = combined_data['ActionGeo_Lat'].min()
max_lat = combined_data['ActionGeo_Lat'].max()
min_long = combined_data['ActionGeo_Long'].min()
max_long = combined_data['ActionGeo_Long'].max()

# Add a blue rectangle to the map
folium.Rectangle(
    bounds=[[min_lat, min_long], [max_lat, max_long]],
    color='blue',
    fill=False
).add_to(m)

# Display the updated map
m

In [12]:
combined_data.to_csv('csv/data.csv', index=False)